In [ ]:
%matplotlib inline

import numpy as np, matplotlib as mpl, scipy as sp, networkx as nx
from matplotlib import pylab, mlab, pyplot as plt
from matplotlib.pylab import plot, scatter, contour, xlabel, ylabel, title, legend
from matplotlib.animation import FuncAnimation
from tqdm.notebook import tqdm, trange

from numpy import sqrt, pi, exp, log, floor, ceil, sin, cos
from numpy import linspace, arange, empty, zeros, ones, empty_like, zeros_like, ones_like
from numpy.linalg import norm

plt.rcParams.update({
    'image.cmap': 'coolwarm',
    'animation.html': 'jshtml',
    'animation.embed_limit': 40, # 40 mb
})
rng = np.random.default_rng()

In [ ]:
N = 200
xx = linspace( -1, 1, num=N )
dx = xx[1] - xx[0]

f = lambda x: \
    -log( exp( -(x - .5)**2 / 2 / .2**2 ) + 1.3*exp( -(x+.5)**2 / 2 / .3**2 ) )

plot( xx, f(xx), label='f' )
legend()
#plt.savefig( 'figures/anneal-f.svg' )

In [ ]:
def anneal( X0, ββ ):
    n_reals = X0.shape[-1]
    X = X0.copy()

    for β in ββ:
        ξ = rng.choice( [-dx, dx], size=n_reals )
        Y = np.fmax( np.fmin( X + ξ, 1 ), -1 )
        U = rng.uniform( size=n_reals )
        accept_mask = ( log(U) < -β*( f(Y) - f(X) ) )
        X[accept_mask] = Y[accept_mask]

    return X

# Running simulated annealing without changing β is the same as running MCMC
def mcmc( X0, β, n_iters ):
    return anneal( X0, tqdm( np.full( n_iters, β ) ) )

In [ ]:
n_reals = 10000
#X0 = rng.choice( xx, size=n_reals )
X0 = np.full( n_reals, .5 )

β = 10
X = mcmc( X0, β, 10000 )

In [ ]:
_ = plt.hist( X, density=True, bins=n_reals//100, label='X' )
Z = np.trapezoid( exp( -β*f(xx)), xx )
π = exp( -β*f(xx) )/Z
plot( xx, π, label=r'$\pi \propto e^{-βf}$' )
legend()
#plt.savefig( 'figures/anneal-mcmc.svg' )

In [ ]:
n_reals = 10000
#X0 = rng.choice( xx, size=n_reals )
X0 = np.full( n_reals, .5 )

ββ = np.logspace( -3, 1, num=10000 )
X = anneal( X0, tqdm(ββ, total=len(ββ)) )

In [ ]:
_ = plt.hist( X, density=True, bins=n_reals//100, label='$X$' )
β = ββ[-1]
Z = np.trapezoid( exp( -β*f(xx)), xx )
π = exp( -β*f(xx) )/Z
plot( xx, π, label=r'$\pi \propto e^{-βf}$' )
legend()
#plt.savefig( 'figures/anneal-anneal.svg' )